<img src="pic/ex05.png" width="100%"> <br>

<h1 class="jp-toc-ignore">ICON Training - Hands-on Session</h1>

# Exercise 5: Programming ICON

---

<table style="width:100%; border-collapse:separate; border-spacing:0;">
  <tr>
    <td style="vertical-align:top; padding-right:20px; line-height:1.8;">
      In this step-by-step exercise we will learn how to <b>implement new variables in the ICON source code</b>.<br><br>
      In the first and relatively easy part of the exercise we will modify the <b>Fortran code</b> directly:
      <ul style="line-height:1.8;">
        <li><b>Step F1</b>: We learn how to allocate new ICON variables. As a by-product we will visualize ICON's domain decomposition.</li>
        <li><b>Optional Exercise</b>: Looping over grid points in Fortran, distinguishing between prognostic cells and halo cells.</li>
      </ul>
    </td>
    <td style="vertical-align:top; text-align:right;">
      <img src="pic/logo_fortran.png" style="height:120px;">
    </td>
  </tr>
</table>


## Step F1: Allocating Additional Fields in the Fortran Code

In the following we will allocate a new ICON variable **directly in the Fortran code**. As a by-product we will visualize ICON's domain decomposition.

Details are given in Section 9.4 of the ICON Tutorial (see the link at the bottom of the page).

<div class="alert alert-success">
    <b style="color:#2d4b9b;">Exercise:</b> 
    Create a fresh copy of the ICON source code at <code>/scratch/${USER::1}/$USER/icon</code>. To this end, follow these steps closely:
</div>

In [ ]:
 export SCRATCHDIR=/scratch/${USER::1}/$USER
 export ICONDIR=${SCRATCHDIR}/icon

Download the release [ICON-2025.04-1](https://gitlab.dkrz.de/icon/icon-model/-/releases) as follows:

In [ ]:
( cd ${SCRATCHDIR}
  git clone --recursive --branch release-2025.04-public https://gitlab.dkrz.de/icon/icon-model.git icon )

<div class="alert alert-info">
<b>A brief digression: </b>
Before we proceed, we will explain some additional steps required to build ICON with support for the <b>YAC coupler</b> and the <b>ICON Community Interface ComIn</b>. The following notebook cell is not strictly necessary but more for informational purposes, as we will return to using our pre-built ICON binary in later exercises where we make use of these libraries.
<p/>
For the YAC library we need to install <code>cython</code>, a tool that allows us to create interfaces between C or C++ and Python. We also modify the wrapper script with an additional linker flag:
Adding <code>-Wl,--export-dynamic-symbol=yac_*</code> to both the host model and plugin linking flags ensures YAC is only loaded once, preventing duplicate copies of its internal lookup table.
</div>

In [ ]:
cd $ICONDIR
pip install cython

sed -i 's|LDFLAGS="${LDFLAGS}"|LDFLAGS="${LDFLAGS} -Wl,--export-dynamic"|' config/dkrz/levante.gcc-11.2.0

We then execute the configure wrapper for the 'Levante' platform with the GCC compiler (`config/dkrz/levante.gcc`) in our local copy of the ICON code.

These steps are fully documented in the [ICON Quickstart Guide](https://icon.gitlab-pages.dkrz.de/icon/buildrun/buildrun_quickstart.html#ref-buildrun-quickstart).

We set several options:

- `--enable-comin`  
   Enables the use of the ICON Community Interface (ComIn), a plugin mechanism which will be used in later exercises.
- `--enable-bundled-python`  
  enables the Python interfaces for ComIn.
- `--disable-jsbach`  
   Disables the [JSBACH land surface model](https://docs.icon-model.org/land/land.html#ref-land-jsbach), which simulates land biosphere processes such as vegetation, soil, carbon, and water cycles.
- `--disable-quincy`  
   Disables the [QUINCY land surface model](https://docs.icon-model.org/land/land.html#quincy), an alternative model for land surface biogeochemistry and vegetation.
- `--disable-rte-rrtmgp`  
   Disables the RTE+RRTMGP radiation scheme, an advanced radiative transfer model for calculating radiative fluxes and heating rates in the atmosphere.

In [ ]:
mkdir -p $ICONDIR/build
cd $ICONDIR/build

../config/dkrz/levante.gcc \
  --enable-comin --disable-jsbach --disable-quincy --disable-rte-rrtmgp --enable-bundled-python  --disable-silent-rules \
> configure.log

Now the ICON code is ready and can be compiled with `make` in the following exercise.

<div class="alert alert-info">
<b>Remark (again):</b> Note that we will not be using the Python bindings for this exercise. However, the YAC coupler and the Community Interface plugins rely on them. These will be discussed in later exercises.
</div>

### Perform the following changes step-by-step:

Just to ensure that our experiment directory is in the correct location:

In [ ]:
export SCRATCHDIR=/scratch/${USER::1}/$USER

* In the subdirectory <code>src/atm_dyn_iconam</code> open the module <code>mo_nonhydro_<b style="color:#D0312D;">types</b></code>.<br/>
  This file contains important structure declarations, i.e. the names and characteristics of the data objects in the atmospheric model:
  * Insert a new 2D variable pointer <code>process_id</code> of type <code>REAL(wp)</code> to the derived type <code>TYPE(t_nh_diag)</code>.<p/>
* Open the module <code>mo_nonhydro_<b style="color:#D0312D;">state</b></code> in the same subdirectory. <br/>
  This file allocates the storage for the above data objects.
  * At the end of the subroutine <code>new_nh_state_diag_list</code>
    * set appropriate metadata variables for NetCDF.
    
      (<code>standard_name</code>, <code>units</code>, <code>long_name</code>, <code>datatype</code>; see <code>t_cf_var</code>)

    * set the metadata also for GRIB2.
    
      (You may use dummy numbers: <code>discipline = parameterCategory = parameterNumber = 255</code>)
    * place the <code>add_var</code> call for the new field.

  * Now, after the <code>add_var</code> call, the new field has been allocated. Fill the data array with a constant value:
    * <code>process_id(:,:) = get_my_mpi_work_id()</code>
  
      This auxiliary function from the source code module <code>mo_mpi</code> returns the MPI rank of the processor (see Section 9.2.4 of the [ICON tutorial](icon_exercise_programming.ipynb#Further-Reading-and-Resources)).

<div class="alert alert-success">
    <b style="color:#2d4b9b;">Exercise:</b> 
    Modify the ICON source code according to the steps above.
</div>

<details>
<summary style="font-size: 1.1em;">Solution</summary>

* [mo_nonhydro_types.f90](reference/F1_additional_field/mo_nonhydro_types.f90)
* [mo_nonhydro_state.f90](reference/F1_additional_field/mo_nonhydro_state.f90)

(Search for <code>EX5:ProgrammingICON:AllocatingFields</code>)

</details>

<br/>

### Build Process

<div class="alert alert-success">
    <b style="color:#2d4b9b;">Exercise:</b> 
    In your local copy of the ICON code, change to the <code>build</code> directory, where we have executed the configure wrapper for the "Levante" platform with the <code>gcc</code> compiler (<code>config/dkrz/levante.gcc</code>, see above).<p/>
    Execute <code>make</code> with 4 processes.
    <br/>
    Due to the large amount of log output during the configuration and compiling, we highly recommend <b>performing this exercise in a terminal window</b>. <p/> <p/><button data-commandlinker-command="terminal:create-new">Create Terminal</button>
</div>

In [ ]:
export ICONDIR=$SCRATCHDIR/icon

...

<details>
<summary style="font-size: 1.1em;">Solution</summary>

```
export SCRATCHDIR=/scratch/${USER::1}/$USER
export ICONDIR=$SCRATCHDIR/icon
cd $ICONDIR/build

make -j4 2>&1 > compile.log
```
</details>

<br/>

### Run the ICON model & visualize the results

<table border="0" cellspacing="0" cellpadding="0" style="width:100%; border-collapse:collapse;">
  <tr>
    <td style="vertical-align:top; padding-right:24px;">     
        <ul>
          <li>
            Use the script <a href="scripts/icon_exercise_programming_run.ipynb"><code>icon_exercise_programming_run.ipynb</code></a> to run ICON.
          </li>
          <li>
            Visualize the results using the script <a href="scripts/icon_exercise_programming_plot01.ipynb"><code>icon_exercise_programming_plot01.ipynb</code></a> and compare it to the reference solution on the right.
          </li>
        </ul>
    </td>
    <td style="vertical-align:top; text-align:right;">
      <figure>
        <img src="reference/F1_additional_field/domain_decomp.png" width="600">
<figcaption style="text-align:center"><em>Reference solution for "Step F1: Allocating Additional Fields".</em> </figcaption>
      </figure>
    </td>
  </tr>
</table>


<div class="alert alert-success">
    <b style="color:#2d4b9b;">Exercise:</b> 
    Why is the output field not a <u>constant</u> value?
</div>

<details>
<summary style="font-size: 1.1em;">Solution</summary>

Each PE writes a different (constant) value - its MPI rank.

</details>

<br/>

<div class="alert alert-success">
    <b style="color:#2d4b9b;">Exercise:</b> 
    Take a closer look at the data: Can you guess why the output field does not only contain <u>integer</u> values?
</div>

<details>
<summary style="font-size: 1.1em;">Solution</summary>

This is a lat-lon interpolated field; although the original field has only integer values, we get intermediate values in the lat-lon interpolation.

</details>

<br/>

### Optional Exercise: Looping over grid points in Fortran

<div class="alert alert-success">
    <b style="color:#2d4b9b;">Optional Exercise:</b> 
    Assign the variable <code>process_id</code> to the MPI rank of the processor only for prognostic cells. For all other cells, set <code>process_id</code> to -1. To achieve this, you must write loops that iterate over the prognostic cells.
</div>

<figure style="float:right;">
<img src="pic/index_ordering_exercise_illustration01.png" width="700">
</figure>

**Explanation of looping in ICON**

For more detailed information, refer to Section 9.3 of the ICON tutorial (see the link at the bottom of the page).


* In order to enhance computational efficiency, loops that iterate over grid cells, edges, and vertices are structured using nested loops, which are known as `jb` loops and `jc` loops. The jb loop is typically employed as the outer loop and is often parallelized using OpenMP.
* This approach involves breaking down a long vector into smaller chunks of length `nproma`. The long vector is stored in a two-dimensional array, where the first index represents the number of elements within a block (`jc`), and the second index represents the number of blocks (`jb`). 
* Upon examination of the figure above (Figure 9.2 in the ICON tutorial), it becomes apparent that by selecting the `start_idx` (start index for looping over the blocks) and `end_idx` (end index for looping over the blocks), one can determine which cell types (boundary regions, prognostic cells, or halo cells) to include in the loop. 
* In the event that `nproma` does not divide the number of cells evenly, the final block may not be completely filled. It therefore is necessary that for each block (`jb`), the start and end indices of the elements within the block are calculated. The auxiliary function `get_indices_c` in ICON assists in computing these indices. 


**Hints:**
* Open the module `mo_nh_stepping` (subdirectory `src/atm_dyn_iconam`). 
    * Create an (empty) subroutine.
    * Place a call to this subroutine immediately before the call to the output routine in the timeloop.
    * Fill your subroutine with a 2D loop over all prognostic grid points, see p. 205 of the ICON tutorial (see the link at the bottom of the page) for help.

<details>
<summary style="font-size: 1.1em;">Solution</summary>

* [mo_nonhydro_types.f90](reference/F1_optional_exercise/mo_nonhydro_types.f90)
* [mo_nonhydro_state.f90](reference/F1_optional_exercise/mo_nonhydro_state.f90)
* [mo_nh_stepping.f90](reference/F1_optional_exercise/mo_nh_stepping.f90)

(Search for <code>EX5:ProgrammingICON:LoopOverGridPoints</code>)

</details>

---

<h2 class="jp-toc-ignore"> <b style="color:#2d4b9b;"><b style="color:#2d4b9b;"> Congratulations! You have successfully completed Exercise 5.</b></h2>

---

## Further Reading and Resources

- ICON Tutorial, Ch. 9: <a href="https://www.dwd.de/DE/leistungen/nwv_icon_tutorial/nwv_icon_tutorial.html">https://www.dwd.de/DE/leistungen/nwv_icon_tutorial/nwv_icon_tutorial.html</a>
  <br/>A new <b>draft version</b> of the ICON Tutorial is available here: <a href="https://icon-training-2025-scripts-rendering-cc74a6.gitlab-pages.dkrz.de/index.html">https://icon-training-2025-scripts-rendering-cc74a6.gitlab-pages.dkrz.de/index.html</a>. It is currently being finalized and will be published soon.

---

*Author info: Deutscher Wetterdienst (DWD) 2025 ::  icon@dwd.de. For a full list of contributors, see CONTRIBUTING in the root directory. License info: see LICENSE file.*